<a href="https://colab.research.google.com/github/jvmedenilla/cancer_detection_flask/blob/main/cancer_detection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
import os
import sys

drive.mount('/content/drive/')
os.chdir("/content/drive/MyDrive/")
sys.path.append('.')
%autosave 60

Mounted at /content/drive/


Autosaving every 60 seconds


# Download cancer-data from Kaggle
First part is download the dataset from Kaggle by downloading kaggle.json to access kaggle API. Then, download the cancer-data dataset.

In [2]:
# Load dataset from Kaggle
!pip install kaggle

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [3]:
!mkdir ~/.kaggle

In [4]:
!cp kaggle.json ~/.kaggle/

In [5]:
!chmod 600 ~/.kaggle/kaggle.json

In [6]:
!kaggle datasets download -d erdemtaha/cancer-data

  0% 0.00/48.6k [00:00<?, ?B/s]
100% 48.6k/48.6k [00:00<00:00, 3.49MB/s]


In [7]:
!mv cancer-data.zip cancer_detection

In [8]:
%cd cancer_detection/

/content/drive/MyDrive/cancer_detection


In [9]:
#!unzip cancer-data.zip

In [10]:
!ls

Cancer_Data.csv  cancer-data.zip  cancer_detection  model.pkl


# Dataset Pre-processing
Next step is do some pre-processing work on the dataset before I use it for my model.

In [11]:
import pandas as pd

df = pd.read_csv('Cancer_Data.csv')
print(df)

           id diagnosis  radius_mean  texture_mean  perimeter_mean  area_mean  \
0      842302         M        17.99         10.38          122.80     1001.0   
1      842517         M        20.57         17.77          132.90     1326.0   
2    84300903         M        19.69         21.25          130.00     1203.0   
3    84348301         M        11.42         20.38           77.58      386.1   
4    84358402         M        20.29         14.34          135.10     1297.0   
..        ...       ...          ...           ...             ...        ...   
564    926424         M        21.56         22.39          142.00     1479.0   
565    926682         M        20.13         28.25          131.20     1261.0   
566    926954         M        16.60         28.08          108.30      858.1   
567    927241         M        20.60         29.33          140.10     1265.0   
568     92751         B         7.76         24.54           47.92      181.0   

     smoothness_mean  compa

In [12]:
df['diagnosis'].replace({'B': 0, 'M': 1}, inplace=True)

In [13]:
import seaborn as sn
import matplotlib.pyplot as plt

df_corr = df.corr()
#sn.heatmap(corr_matrix, annot=True)
#plt.show()
plt.figure(figsize=(20, 20),dpi=600)
g=sn.heatmap(df_corr, square=True,
            center=0, annot=True, linewidths=.5,
            cmap="RdBu_r", cbar_kws={"shrink": 0.8},vmin=-1,vmax=1);
g.set_xticklabels(g.get_xticklabels(),rotation=45,fontsize=8,ha='right')
plt.title('Correlation Matrix')

Text(0.5, 1.0, 'Correlation Matrix')

In [14]:
relevant_features = df_corr['diagnosis'].sort_values(ascending=False)
features_list = list(relevant_features[1:10].keys())
irrelevant_features = list(relevant_features[10:].keys())
#print(irrelevant_features)
for item in irrelevant_features:
  df.drop(item, inplace=True, axis=1)

df

diagnosis  radius_mean  perimeter_mean  area_mean  concavity_mean  \
0            1        17.99          122.80     1001.0         0.30010   
1            1        20.57          132.90     1326.0         0.08690   
2            1        19.69          130.00     1203.0         0.19740   
3            1        11.42           77.58      386.1         0.24140   
4            1        20.29          135.10     1297.0         0.19800   
..         ...          ...             ...        ...             ...   
564          1        21.56          142.00     1479.0         0.24390   
565          1        20.13          131.20     1261.0         0.14400   
566          1        16.60          108.30      858.1         0.09251   
567          1        20.60          140.10     1265.0         0.35140   
568          0         7.76           47.92      181.0         0.00000   

     concave points_mean  radius_worst  perimeter_worst  area_worst  \
0                0.14710        25.380           184.60      2019.0   
1                0.07017        24.990           158.80      1956.0   
2                0.12790        23.570           152.50      1709.0   
3                0.10520        14.910            98.87       567.7   
4                0.10430        22.540           152.20      1575.0   
..                   ...           ...              ...         ...   
564              0.13890        25.450           166.10      2027.0   
565              0.09791        23.690           155.00      1731.0   
566              0.05302        18.980           126.70      1124.0   
567              0.15200        25.740           184.60      1821.0   
568              0.00000         9.456            59.16       268.6   

     concave points_worst  
0                  0.2654  
1                  0.1860  
2                  0.2430  
3                  0.2575  
4                  0.1625  
..                    ...  
564                0.2216  
565                0.1628  
566                0.1418  
567                0.2650  
568                0.0000  

[569 rows x 10 columns]

In [15]:
df_data = df.copy(deep=True)

In [16]:
df_target = df['diagnosis']
df_data = df.drop(columns='diagnosis')

In [17]:
df_target.replace({1:True, 0:False}, inplace=True)
df_target

0       True
1       True
2       True
3       True
4       True
       ...  
564     True
565     True
566     True
567     True
568    False
Name: diagnosis, Length: 569, dtype: bool

In [18]:
df_target.unique()

array([ True, False])

In [19]:
df_data

radius_mean  perimeter_mean  area_mean  concavity_mean  \
0          17.99          122.80     1001.0         0.30010   
1          20.57          132.90     1326.0         0.08690   
2          19.69          130.00     1203.0         0.19740   
3          11.42           77.58      386.1         0.24140   
4          20.29          135.10     1297.0         0.19800   
..           ...             ...        ...             ...   
564        21.56          142.00     1479.0         0.24390   
565        20.13          131.20     1261.0         0.14400   
566        16.60          108.30      858.1         0.09251   
567        20.60          140.10     1265.0         0.35140   
568         7.76           47.92      181.0         0.00000   

     concave points_mean  radius_worst  perimeter_worst  area_worst  \
0                0.14710        25.380           184.60      2019.0   
1                0.07017        24.990           158.80      1956.0   
2                0.12790        23.570           152.50      1709.0   
3                0.10520        14.910            98.87       567.7   
4                0.10430        22.540           152.20      1575.0   
..                   ...           ...              ...         ...   
564              0.13890        25.450           166.10      2027.0   
565              0.09791        23.690           155.00      1731.0   
566              0.05302        18.980           126.70      1124.0   
567              0.15200        25.740           184.60      1821.0   
568              0.00000         9.456            59.16       268.6   

     concave points_worst  
0                  0.2654  
1                  0.1860  
2                  0.2430  
3                  0.2575  
4                  0.1625  
..                    ...  
564                0.2216  
565                0.1628  
566                0.1418  
567                0.2650  
568                0.0000  

[569 rows x 9 columns]

# Model Selection

Now that I have identified the key features, it's time run a model. I am going to use XGBoost as my classifier.

In [20]:
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.model_selection import train_test_split
import xgboost as xgb
import pickle

X = df_data
Y = df_target

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.20, random_state=7)

xgb_model = xgb.XGBClassifier(objective='binary:logistic', random_state=42)
xgb_model.fit(X_train,y_train)

# save model in pickle
pickle.dump(xgb_model, open('model.pkl', 'wb'))
model = pickle.load(open('model.pkl', 'rb'))

y_pred = model.predict(X_test)
predictions = [round(value) for value in y_pred]
accuracy = accuracy_score(y_test, predictions)


print(confusion_matrix(y_test, y_pred))
print("Accuracy: %.2f%%" % (accuracy*100))

[[74  0]
 [ 4 36]]
Accuracy: 96.49%


In [21]:
features = list(X_test.keys())
features

['radius_mean',
 'perimeter_mean',
 'area_mean',
 'concavity_mean',
 'concave points_mean',
 'radius_worst',
 'perimeter_worst',
 'area_worst',
 'concave points_worst']

In [22]:
import numpy as np
feature_dict = {}
#for item in features:
#  feature_dict[item] = [2]

radius_mean = 0.1
perimeter_mean = 0.1
area_mean = 0.1
concavity_mean = 0.1
concave_points_mean = 0.1
radius_worst = 0.1
perimeter_worst = 0.1
area_worst = 0.1
concave_points_worst = 0.1

request_values = {'radius_mean':radius_mean, 'perimeter_mean': perimeter_mean, 'area_mean':area_mean, 'concavity_mean': concavity_mean,
                  'concave points_mean': concave_points_mean, 'radius_worst': radius_worst, 'perimeter_worst': perimeter_worst,
                  'area_worst': area_worst, 'concave points_worst': concave_points_worst}


print(request_values.values())
df_feature = pd.DataFrame(request_values, index=[0])
print(df_feature)

sample_pred = model.predict(df_feature)[0]
print(sample_pred)

dict_values([0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1])
   radius_mean  perimeter_mean  area_mean  concavity_mean  \
0          0.1             0.1        0.1             0.1   

   concave points_mean  radius_worst  perimeter_worst  area_worst  \
0                  0.1           0.1              0.1         0.1   

   concave points_worst  
0                   0.1  
0


In [23]:
df_feature.keys()

Index(['radius_mean', 'perimeter_mean', 'area_mean', 'concavity_mean',
       'concave points_mean', 'radius_worst', 'perimeter_worst', 'area_worst',
       'concave points_worst'],
      dtype='object')